In [1]:
# Notebook parameters. Values here are for development only and 
# will be overridden when running via snakemake and papermill.
cohort_id = "CD-NU_Gbadolite_gamb_2015_Q3"
# cohort_id = 'ML-2_Kati_colu_2014_Q3'
# cohort_id = 'CI-LG_Agneby-Tiassa_colu_2012'
cohorts_analysis = "20230223"
contigs = ['2RL', '3RL', 'X']
sample_sets = "3.0"
min_cohort_size = 20
max_cohort_size = 50
h12_calibration_contig = '3L'
use_gcs_cache = False
dask_scheduler = "threads"

In [2]:
# Parameters
min_cohort_size = 20
max_cohort_size = 50
sample_sets = ["3.0"]
contigs = ["2RL", "3RL", "X"]
cohorts_analysis = "20230223"
h12_calibration_contig = "3L"
h12_signal_detection_min_delta_aic = 1000
h12_signal_detection_min_stat_max = 0.1
h12_signal_detection_gflanks = [6]
use_gcs_cache = False
dask_scheduler = "single-threaded"
cohort_id = "ML-3_Yanfolila_gamb_2012_Q4"


In [3]:
from IPython.display import Markdown, HTML
import malariagen_data
import numpy as np
import pandas as pd
from pyprojroot import here
import yaml
import dask
dask.config.set(scheduler=dask_scheduler);
from textwrap import dedent

import geopandas as gpd
import bokeh.layouts as bklay
import bokeh.plotting as bkplt
import bokeh.models as bkmod
import plotly.express as px

from bokeh.io import output_notebook # enables plot interface in J notebook

# N.B., do not add the "remove-output" tag to this cell!!! If you do,
# the bokeh javascript libraries will not get loaded in the generated
# HTML page. The call to output_notebook() injects javascript in the
# cell output which triggers the bokeh javascript libraries to be loaded
# in the page.
output_notebook(hide_banner=True)

# Mali / Yanfolila / gambiae / 2012 / Q4

In [4]:
# Load cohorts to find sample query to select samples for this cohort.

df_cohorts = gpd.read_file(here() / "build" / "final_cohorts.geojson").set_index("cohort_id")
cohort = df_cohorts.loc[cohort_id]
cohort

cohort_size                                                          53
country                                                            Mali
admin1_iso                                                         ML-3
admin1_name                                                     Sikasso
admin2_name                                                   Yanfolila
taxon                                                           gambiae
year                                                               2012
quarter                                                               4
cohort_label                     Mali / Yanfolila / gambiae / 2012 / Q4
sample_query          cohort_admin2_quarter == 'ML-3_Yanfolila_gamb_...
latitude                                                      10.879231
longitude                                                         -7.85
h12_window_size                                                  1000.0
country_alpha2                                                  

In [5]:
# Initialise access to MalariaGEN data.

extra_params = dict()
if use_gcs_cache:
    extra_params["url"] = "simplecache::gs://vo_agam_release"
    extra_params["simplecache"] = dict(cache_storage=(here() / "gcs_cache").as_posix())

ag3 = malariagen_data.Ag3(
    # Pin the version of the cohorts analysis for reproducibility.
    cohorts_analysis=cohorts_analysis,
    results_cache=(here() / "malariagen_data_cache").as_posix(),
    **extra_params,
)
ag3

<MalariaGEN Ag3 API client>
Storage URL             : gs://vo_agam_release/
Data releases available : 3.0, 3.1, 3.2, 3.3, 3.4, 3.5, 3.6, 3.7, 3.8
Results cache           : /home/sanjaynagi/selection-atlas/malariagen_data_cache
Cohorts analysis        : 20230223
AIM analysis            : 20220528
Site filters analysis   : dt_20200416
Software version        : malariagen_data 7.13.0
Client location         : unknown
---
Please note that data are subject to terms of use,
for more information see https://www.malariagen.net/data
or contact data@malariagen.net. For API documentation see 
https://malariagen.github.io/vector-data/ag3/api.html

In [6]:
# Load sample metadata for this cohort.

df_samples = ag3.sample_metadata(sample_query=cohort['sample_query'])
df_samples

sample_id partner_sample_id  contributor country        location  year  \
0   AV0330-C            KV1269  Ken Vernick    Mali  Toumani Oulena  2012   
1   AV0342-C            KV1294  Ken Vernick    Mali  Toumani Oulena  2012   
2   AV0354-C            KV1285  Ken Vernick    Mali  Toumani Oulena  2012   
3   AV0377-C            KV1298  Ken Vernick    Mali  Toumani Oulena  2012   
4   AV0387-C            KV1303  Ken Vernick    Mali  Toumani Oulena  2012   
5   AV0407-C            KV1326  Ken Vernick    Mali  Toumani Oulena  2012   
6   AV0367-C            KV1337  Ken Vernick    Mali  Toumani Oulena  2012   
7   AV0378-C            KV1339  Ken Vernick    Mali  Toumani Oulena  2012   
8   AV0408-C            KV1352  Ken Vernick    Mali  Toumani Oulena  2012   
9   AV0332-C            KV1355  Ken Vernick    Mali  Toumani Oulena  2012   
10  AV0344-C            KV1357  Ken Vernick    Mali  Toumani Oulena  2012   
11  AV0356-C            KV1370  Ken Vernick    Mali  Toumani Oulena  2012   
12  AV0368-C            KV1371  Ken Vernick    Mali  Toumani Oulena  2012   
13  AV0389-C            KV1378  Ken Vernick    Mali  Toumani Oulena  2012   
14  AV0409-C            KV1395  Ken Vernick    Mali  Toumani Oulena  2012   
15  AV0333-C            KV1397  Ken Vernick    Mali  Toumani Oulena  2012   
16  AV0380-C            KV1404  Ken Vernick    Mali  Toumani Oulena  2012   
17  AV0390-C            KV1405  Ken Vernick    Mali  Toumani Oulena  2012   
18  AV0400-C            KV1407  Ken Vernick    Mali  Toumani Oulena  2012   
19  AV0410-C            KV1410  Ken Vernick    Mali  Toumani Oulena  2012   
20  AV0334-C            KV1414  Ken Vernick    Mali  Toumani Oulena  2012   
21  AV0346-C            KV1416  Ken Vernick    Mali  Toumani Oulena  2012   
22  AV0358-C            KV1419  Ken Vernick    Mali  Toumani Oulena  2012   
23  AV0381-C            KV1423  Ken Vernick    Mali  Toumani Oulena  2012   
24  AV0391-C            KV1427  Ken Vernick    Mali  Toumani Oulena  2012   
25  AV0401-C            KV1430  Ken Vernick    Mali  Toumani Oulena  2012   
26  AV0335-C            KV1440  Ken Vernick    Mali  Toumani Oulena  2012   
27  AV0347-C            KV1444  Ken Vernick    Mali  Toumani Oulena  2012   
28  AV0359-C            KV1451  Ken Vernick    Mali  Toumani Oulena  2012   
29  AV0371-C            KV1453  Ken Vernick    Mali  Toumani Oulena  2012   
30  AV0382-C            KV1454  Ken Vernick    Mali  Toumani Oulena  2012   
31  AV0392-C            KV1458  Ken Vernick    Mali  Toumani Oulena  2012   
32  AV0402-C            KV1462  Ken Vernick    Mali  Toumani Oulena  2012   
33  AV0412-C            KV1466  Ken Vernick    Mali  Toumani Oulena  2012   
34  AV0336-C            KV1468  Ken Vernick    Mali  Toumani Oulena  2012   
35  AV0360-C            KV1476  Ken Vernick    Mali  Toumani Oulena  2012   
36  AV0372-C            KV1480  Ken Vernick    Mali  Toumani Oulena  2012   
37  AV0383-C            KV1484  Ken Vernick    Mali  Toumani Oulena  2012   
38  AV0393-C            KV1485  Ken Vernick    Mali  Toumani Oulena  2012   
39  AV0403-C            KV1486  Ken Vernick    Mali  Toumani Oulena  2012   
40  AV0361-C            KV1583  Ken Vernick    Mali  Toumani Oulena  2012   
41  AV0384-C            KV1592  Ken Vernick    Mali  Toumani Oulena  2012   
42  AV0338-C            KV1599  Ken Vernick    Mali  Toumani Oulena  2012   
43  AV0350-C            KV1602  Ken Vernick    Mali  Toumani Oulena  2012   
44  AV0405-C            KV1614  Ken Vernick    Mali  Toumani Oulena  2012   
45  AV0351-C            KV1619  Ken Vernick    Mali  Toumani Oulena  2012   
46  AV0363-C            KV1620  Ken Vernick    Mali  Toumani Oulena  2012   
47  AV0386-C            KV1623  Ken Vernick    Mali  Toumani Oulena  2012   
48  AV0406-C            KV1625  Ken Vernick    Mali  Toumani Oulena  2012   
49  AV0376-C            KV1314  Ken Vernick    Mali  Toumani Oulena  2012   
50  AV0263-C            KV1046  Ken Vernick    Mali           Takan  2012   

In [7]:
# Determine collection dates.

df_collection_dates = (
    df_samples
    .groupby(["year", "month"])
    .size()
    .reset_index()
    .rename(columns={0: 'count'})
)
df_collection_dates

year  month  count
0  2012     10     53

In [8]:
# Determine first and last collection months.

min_month = df_collection_dates["month"].min()
max_month = df_collection_dates["month"].max()

if min_month < 0:
    start_month = end_month = None
else:
    start_month = pd.to_datetime(min_month, format="%m").month_name()
    end_month = pd.to_datetime(max_month, format="%m").month_name()
    
start_month, end_month

('October', 'October')

In [9]:
# Determine unique collection locations.

df_locations = df_samples[["location", "longitude", "latitude"]].drop_duplicates()
df_locations

location  longitude  latitude
0   Toumani Oulena      -7.81     10.83
50           Takan      -8.33     11.47

In [10]:
# Extract provenance information about the samples.

df_contributors = df_samples[["release", "sample_set", "contributor"]].drop_duplicates()
df_contributors["study"] = df_contributors.apply(
    lambda v: "Ag1000G" if v["sample_set"].startswith("AG1000G") else "TODO",
    axis="columns"
)
df_contributors["release"] = df_contributors["release"].apply(
    lambda v: f"Ag{v}"
)
df_contributors.rename(columns={
    "contributor": "Contributor",
    "study": "Study",
    "release": "Data release",
    "sample_set": "Sample set",
}, inplace=True)
df_contributors.set_index(["Contributor", "Study", "Data release"], inplace=True)
df_contributors

Sample set
Contributor Study   Data release              
Ken Vernick Ag1000G Ag3.0         AG1000G-GN-B

In [11]:
# Build a paragraph with summary information about the samples in this cohort.

n_locations = len(df_locations)

summary_info = f"""This cohort comprises {cohort['cohort_size']:,} samples from the 
*{cohort['taxon']}* taxon, collected from {n_locations} locations within the administrative 
division of {cohort['admin2_name']}, {cohort['admin1_name']}, {cohort['country']}."""

if start_month and start_month == end_month:
    summary_info += f""" Collections were made in {start_month} {cohort['year']}."""
elif start_month:
    summary_info += f""" Collections were made between {start_month} and {end_month} in {cohort['year']}."""
else:
    summary_info += f""" Collections were made in {cohort['year']}."""
    
display(Markdown(summary_info))


This cohort comprises 53 samples from the 
*gambiae* taxon, collected from 2 locations within the administrative 
division of Yanfolila, Sikasso, Mali. Collections were made in October 2012.

## Selection scans

In [12]:
# load signals to overlay on H12 plots
import pandas as pd

df_signals_contigs = []
for contig in contigs:

    try:
        df_signals_contig = pd.read_csv(here() / "build/h12-signal-detection/" / f"{cohort_id}_{contig}.csv")
    except pd.errors.EmptyDataError:
        df_signals_contig = pd.DataFrame()
    df_signals_contigs.append(df_signals_contig)  
    
df_signals = pd.concat(df_signals_contigs)

# Add extra columns to help with overlaying signals on plots.
df_signals["bottom"] = 0
df_signals["top"] = 1

df_signals

cohort_id contig     gcenter   pcenter  delta_i  \
0  ML-3_Yanfolila_gamb_2012_Q4    2RL   57.011159  28505580     6165   
1  ML-3_Yanfolila_gamb_2012_Q4    2RL  121.003931  64272597     3160   
2  ML-3_Yanfolila_gamb_2012_Q4    2RL  172.633677  90087470     6075   
0  ML-3_Yanfolila_gamb_2012_Q4    3RL   57.081988  28540994     6073   
0  ML-3_Yanfolila_gamb_2012_Q4      X   30.511333  15255667     3738   

   stat_max    gpos_max  ppos_max  focus_gstart  focus_gstop  ...      skew  \
0    0.2630   56.925890  28462945     56.915843    57.159485  ... -0.318993   
1    1.0000  120.074432  63216998    120.675999   121.265286  ...  0.163692   
2    0.3898  172.633678  90087470    172.280316   172.824495  ...  0.444473   
0    0.4630   57.130386  28565193     56.998490    57.170473  ... -0.041850   
0    0.3304   30.493090  15246545     30.372441    30.647890  ...  0.012236   

   decay_left  decay_right  baseline           aic           bic        rss  \
0    0.381263     0.593304  0.022140 -19183.659142 -19155.599930   0.152503   
1    1.311726     1.045420  0.056109  -6854.835071  -6828.235746  16.016454   
2    1.413443     0.763272  0.016980 -15242.292686 -15214.621544   0.539173   
0    0.333990     0.353940  0.027996 -16070.283245 -16042.641587   0.327266   
0    0.555571     0.546226  0.036605 -14362.335400 -14334.524591   1.096510   

   constant_aic  bottom  top  
0 -13017.925818       0    1  
1  -3694.380118       0    1  
2  -9167.048776       0    1  
0  -9997.152632       0    1  
0 -10623.658727       0    1  

[5 rows x 32 columns]

In [13]:
# load window sizes 
h12_calibration_dir = "build/h12-calibration"
with open(here() / h12_calibration_dir / f"{cohort_id}.yaml") as h12_calibration_file:
    h12_calibration_params = yaml.safe_load(h12_calibration_file)
h12_window_size = h12_calibration_params["h12_window_size"]
g123_calibration_dir = "build/g123-calibration"
with open(here() / g123_calibration_dir / f"{cohort_id}.yaml") as g123_calibration_file:
    g123_calibration_params = yaml.safe_load(g123_calibration_file)
g123_window_size = g123_calibration_params["g123_window_size"]

if cohort.taxon == 'arabiensis':
    phasing_analysis = 'arab'
else:
    phasing_analysis = 'gamb_colu'

ihs_window_size = 100

def plot_h12_g123_ihs_tracks(
        contig, 
        df_signals,
        sizing_mode='stretch_width', 
        show=False, 
        width=800, 
        track_height=150,
        genes_height=90,
    ):

    sample_query = cohort["sample_query"]
    
    fig1 = ag3.plot_h12_gwss_track(
        contig=contig, 
        window_size=h12_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        show=show,
        width=width,
        height=track_height,
    )
    fig1.xaxis.visible = False
        
    if not df_signals.empty:
        df = df_signals.query("contig == @contig")
        center_xs = [np.array([row.pcenter, row.pcenter]) for idx, row in df.iterrows()]
        center_ys = [np.array([0, 1]) for idx, row in df.iterrows()]
        source = bkmod.ColumnDataSource(data={
            'cohort': df.cohort_id,
            'chromosome': df.contig,
            'score': df.delta_i.astype(int),
            'peak_start': df.span2_pstart,
            'peak_stop': df.span2_pstop,
            'focus_start': df.focus_pstart,
            'focus_stop': df.focus_pstop,    
            'center_xs': center_xs,
            'center_ys': center_ys,
            'bottom': df.bottom ,
            'top': df.top,
            })
        quad = fig1.quad(bottom='bottom', top='top', left='peak_start', right='peak_stop', 
              source=source, color="gray", alpha=.1, line_width=1)
        quad2 = fig1.quad(bottom='bottom', top='top', left='focus_start', right='focus_stop', 
              source=source, color="red", alpha=.4)
        glyph = bkmod.MultiLine(xs='center_xs', ys='center_ys', line_color='red', line_width=2, line_alpha=0.8)
        fig1.add_glyph(source, glyph)
    
        hover = bkmod.HoverTool(tooltips=[
            ("Cohort", '@cohort'),
            ("Score", '@score'),
            ("Focus", "@focus_start{,} - @focus_stop{,}"),
        ], renderers=[quad])

        fig1.add_tools(hover)
    
    fig2 = ag3.plot_g123_gwss_track(
        contig=contig, 
        window_size=g123_window_size, 
        sites=phasing_analysis,
        site_mask=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig2.xaxis.visible = False

    fig3 = ag3.plot_ihs_gwss_track(
        contig=contig, 
        window_size=ihs_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig3.xaxis.visible = False


    fig4 = ag3.plot_genes(
        region=contig, 
        show=show,
        sizing_mode=sizing_mode,
        width=width,
        height=genes_height,
        x_range=fig1.x_range
        )
                        
    fig = bklay.gridplot(
        [fig1, fig2, fig3, fig4],
        ncols=1,
        toolbar_location="above",
        merge_tools=True,
        sizing_mode=sizing_mode,
    )
    return fig 

In [14]:
for contig in contigs:
    
    display(HTML(f"<h3>Chromosome {contig}</h3>"))
    
    fig = plot_h12_g123_ihs_tracks(
        contig=contig,
        df_signals=df_signals,
    );

    bkplt.show(fig)


## Sampling information

In [15]:
from ipyleaflet import Map, Marker, basemaps
from ipywidgets import HTML

center = cohort[['latitude', 'longitude']].to_list()
m = Map(center=center, zoom=9, basemap=basemaps.OpenTopoMap)

df = df_samples[['latitude', 'longitude', 'taxon']].groupby(['latitude', 'longitude', 'taxon']).size().to_frame().rename(columns={0: 'count'}).reset_index()

for coh_id, row in df.iterrows():
    lat, long = row[['latitude', 'longitude']]
    
    if row['taxon'] == 'gambiae':
        color= 'red'
    elif row['taxon'] == 'coluzzii':
        color='cadetblue'
    elif row['taxon'] == 'arabiensis':
        color='lightgreen'
    else: 
        color='gray'

    marker = Marker(location=(lat, long), draggable=False, opacity=0.7, color=color)
    m.add_layer(marker);

    message2 = HTML()
    message2.value = f"n = {row['count']}"
    marker.popup = message2

display(m)

Map(center=[10.879230769230771, -7.85], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_ti…

In [16]:

if min_month >= 0:
    # For this cohort we have month data, so show a breakdown of sample
    # numbers by location and month.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.pivot_table(
        index=["location", "longitude", "latitude"],
        columns="month",
        values="sample_id",
        aggfunc="count",
        fill_value=0,
    )

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude")] + 
        [("Date", pd.to_datetime(x, format="%m").month_name()) 
         for x in df_loc_dt.columns[3:]], 
    )
    df_loc_dt.columns = cols
    
else:
    # For this cohort we do not have month data, so show a breakdown of sample
    # numbers by location only.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.groupby(["location", "longitude", "latitude"]).agg({"sample_id": "count"})

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude"), ("Date", cohort.year)]
    )
    df_loc_dt.columns = cols

# Style the table.
df_loc_dt_styled = (
    df_loc_dt
    .style
    .format(precision=3)
    .set_caption("Number of samples collected.")
    .hide()
)
display(df_loc_dt_styled)    

## Diagnostics
### H12 calibration

In [17]:
display(Markdown(f"Selected window size: **{h12_window_size:,}**"))

window_sizes = (100, 200, 500, 1000, 2000, 5000, 10000, 20000)

ag3.plot_h12_calibration(
    contig=h12_calibration_contig,
    analysis=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);


Selected window size: **1,000**

### G123 Calibration

In [18]:
display(Markdown(f"Selected window size: **{g123_window_size:,}**"))

ag3.plot_g123_calibration(
    contig=h12_calibration_contig,
    sites=phasing_analysis,
    site_mask=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);

Selected window size: **500**

## Data sources

In [19]:
df_sources_style = (
    df_contributors
    .style
    .set_caption("MalariaGEN Vector Observatory partners, studies and sample sets contributing data for this cohort.")
)
df_sources_style